(TutorialLearner1D)=
# Tutorial {class}`~adaptive.Learner1D`

```{note}
Because this documentation consists of static html, the `live_plot` and `live_info` widget is not live.
Download the notebook in order to see the real behaviour. [^download]
```

In [1]:
import adaptive

adaptive.notebook_extension()

import numpy as np
from functools import partial
import random

## scalar output: `f:ℝ → ℝ`

We start with the most common use-case: sampling a 1D function `f: ℝ → ℝ`.

We will use the following function, which is a smooth (linear) background with a sharp peak at a random location:

In [2]:
offset = random.uniform(-0.5, 0.5)


def f(x, offset=offset, wait=True):
    from time import sleep
    from random import random

    a = 0.01
    if wait:
        sleep(random() / 10)
    return x + a**2 / (a**2 + (x - offset) ** 2)

We start by initializing a 1D “learner”, which will suggest points to evaluate, and adapt its suggestions as more and more points are evaluated.

In [3]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))

Next we create a “runner” that will request points from the learner and evaluate ‘f’ on them.

By default on Unix-like systems the runner will evaluate the points in parallel using local processes {class}`concurrent.futures.ProcessPoolExecutor`.

On Windows systems the runner will use a {class}`loky.get_reusable_executor`.
A {class}`~concurrent.futures.ProcessPoolExecutor` cannot be used on Windows for reasons.

In [4]:
# The end condition is when the "loss" is less than 0.1. In the context of the
# 1D learner this means that we will resolve features in 'func' with width 0.1 or wider.
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [5]:
await runner.task  # This is not needed in a notebook environment!

When instantiated in a Jupyter notebook the runner does its job in the background and does not block the IPython kernel.
We can use this to create a plot that updates as new data arrives:

In [6]:
runner.live_info()

In [7]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

We can now compare the adaptive sampling to a homogeneous sampling with the same number of points:

In [8]:
if not runner.task.done():
    raise RuntimeError(
        "Wait for the runner to finish before executing the cells below!"
    )

In [9]:
learner2 = adaptive.Learner1D(f, bounds=learner.bounds)

xs = np.linspace(*learner.bounds, len(learner.data))
learner2.tell_many(xs, map(partial(f, wait=False), xs))

learner.plot() + learner2.plot()

:Layout
   .Overlay.I  :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.II :Overlay
      .Scatter.I :Scatter   [x]   (y)

## vector output: `f:ℝ → ℝ^N`

Sometimes you may want to learn a function with vector output:

In [10]:
random.seed(0)
offsets = [random.uniform(-0.8, 0.8) for _ in range(3)]

# sharp peaks at random locations in the domain
def f_levels(x, offsets=offsets):
    a = 0.01
    return np.array(
        [offset + x + a**2 / (a**2 + (x - offset) ** 2) for offset in offsets]
    )

`adaptive` has you covered!
The `Learner1D` can be used for such functions:

In [11]:
learner = adaptive.Learner1D(f_levels, bounds=(-1, 1))
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [12]:
await runner.task  # This is not needed in a notebook environment!

/home/docs/checkouts/readthedocs.org/user_builds/adaptive/conda/v0.14.2/lib/python3.9/site-packages/numpy/lib/nanfunctions.py:96: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  a = np.asanyarray(a)


In [13]:
runner.live_info()

In [14]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I   :Scatter   [x]   (y)
      .Scatter.II  :Scatter   [x]   (y)
      .Scatter.III :Scatter   [x]   (y)

## Looking at curvature

By default `adaptive` will sample more points where the (normalized) euclidean distance between the neighboring points is large.
You may achieve better results sampling more points in regions with high curvature.
To do this, you need to tell the learner to look at the curvature by specifying `loss_per_interval`.

In [15]:
from adaptive.learner.learner1D import (
    curvature_loss_function,
    uniform_loss,
    default_loss,
)

curvature_loss = curvature_loss_function()
learner = adaptive.Learner1D(f, bounds=(-1, 1), loss_per_interval=curvature_loss)
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [16]:
await runner.task  # This is not needed in a notebook environment!

In [17]:
runner.live_info()

In [18]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

We may see the difference of homogeneous sampling vs only one interval vs including the nearest neighboring intervals in this plot.
We will look at 100 points.

In [19]:
def sin_exp(x):
    from math import exp, sin

    return sin(15 * x) * exp(-(x**2) * 2)


learner_h = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=uniform_loss)
learner_1 = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=default_loss)
learner_2 = adaptive.Learner1D(sin_exp, (-1, 1), loss_per_interval=curvature_loss)

npoints_goal = lambda l: l.npoints >= 100
# adaptive.runner.simple is a non parallel blocking runner.
adaptive.runner.simple(learner_h, goal=npoints_goal)
adaptive.runner.simple(learner_1, goal=npoints_goal)
adaptive.runner.simple(learner_2, goal=npoints_goal)

(
    learner_h.plot().relabel("homogeneous")
    + learner_1.plot().relabel("euclidean loss")
    + learner_2.plot().relabel("curvature loss")
).cols(2)

:Layout
   .Overlay.Homogeneous    :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Euclidean_loss :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Curvature_loss :Overlay
      .Scatter.I :Scatter   [x]   (y)

More info about using custom loss functions can be found in {ref}`Custom adaptive logic for 1D and 2D`.

## Exporting the data

We can view the raw data by looking at the dictionary `learner.data`.
Alternatively, we can view the data as NumPy array with

In [20]:
learner.to_numpy()

array([[-1.        , -0.99993286],
       [-0.75      , -0.74989381],
       [-0.5       , -0.49980733],
       [-0.375     , -0.37471796],
       [-0.25      , -0.24954822],
       [-0.125     , -0.12416234],
       [ 0.        ,  0.00205498],
       [ 0.0625    ,  0.0664964 ],
       [ 0.125     ,  0.13587527],
       [ 0.15625   ,  0.17999622],
       [ 0.171875  ,  0.21266419],
       [ 0.1875    ,  0.27222095],
       [ 0.1953125 ,  0.33271125],
       [ 0.203125  ,  0.45479731],
       [ 0.20703125,  0.56689212],
       [ 0.2109375 ,  0.7401897 ],
       [ 0.21484375,  0.98098591],
       [ 0.21875   ,  1.19321988],
       [ 0.22070312,  1.21958537],
       [ 0.22265625,  1.17292582],
       [ 0.2265625 ,  0.94929242],
       [ 0.23046875,  0.72548682],
       [ 0.234375  ,  0.57200871],
       [ 0.23828125,  0.47588845],
       [ 0.2421875 ,  0.41577934],
       [ 0.25      ,  0.35224747],
       [ 0.265625  ,  0.31217688],
       [ 0.28125   ,  0.30752055],
       [ 0.3125    ,

If Pandas is installed (optional dependency), you can also run

In [21]:
df = learner.to_dataframe()
df

x         y function.offset function.wait
0  -1.000000 -0.999933        0.220369          True
1  -0.750000 -0.749894        0.220369          True
2  -0.500000 -0.499807        0.220369          True
3  -0.375000 -0.374718        0.220369          True
4  -0.250000 -0.249548        0.220369          True
5  -0.125000 -0.124162        0.220369          True
6   0.000000  0.002055        0.220369          True
7   0.062500  0.066496        0.220369          True
8   0.125000  0.135875        0.220369          True
9   0.156250  0.179996        0.220369          True
10  0.171875  0.212664        0.220369          True
11  0.187500  0.272221        0.220369          True
12  0.195312  0.332711        0.220369          True
13  0.203125  0.454797        0.220369          True
14  0.207031  0.566892        0.220369          True
15  0.210938  0.740190        0.220369          True
16  0.214844  0.980986        0.220369          True
17  0.218750  1.193220        0.220369          True
18  0.220703  1.219585        0.220369          True
19  0.222656  1.172926        0.220369          True
20  0.226562  0.949292        0.220369          True
21  0.230469  0.725487        0.220369          True
22  0.234375  0.572009        0.220369          True
23  0.238281  0.475888        0.220369          True
24  0.242188  0.415779        0.220369          True
25  0.250000  0.352247        0.220369          True
26  0.265625  0.312177        0.220369          True
27  0.281250  0.307521        0.220369          True
28  0.312500  0.324144        0.220369          True
29  0.375000  0.379165        0.220369          True
30  0.437500  0.439617        0.220369          True
31  0.500000  0.501277        0.220369          True
32  0.750000  0.750356        0.220369          True
33  0.875000  0.875233        0.220369          True
34  1.000000  1.000164        0.220369          True

and load that data into a new learner with

In [22]:
new_learner = adaptive.Learner1D(learner.function, (-1, 1))  # create an empty learner
new_learner.load_dataframe(df)  # load the pandas.DataFrame's data
new_learner.plot()

:Overlay
   .Scatter.I :Scatter   [x]   (y)

[^download]: This notebook can be downloaded as **{nb-download}`tutorial.Learner1D.ipynb`** and {download}`tutorial.Learner1D.md`.